# Using TEBD to find the ground state of a nearest-neighbour Hamiltonian

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from tnsbasic.mps import MPS,MPO
import tnsbasic.contractor as contractor
import tnsbasic.operators as op
from tnsbasic.tebd import TEBD

plt.rcParams['figure.figsize'] = [10, 6];

# Pauli matrices, to construct spin operators

sigma0=np.identity(2);
sigmaX=np.array([[0,1.],[1.,0]]);
sigmaY=np.array([[0,-1j],[1j,0]]);
sigmaZ=np.array([[1.,0],[0,-1.]]);

## Ising Hamiltonian

For our first example, we construct the two-body terms of the Ising Hamiltonian 
$$H=\sum_i J \sigma_z^{[i]} \sigma_z^{[i+1]}+g\sigma_x^{[i]}$$
We build a list of terms, and, for convenience, also write it as a MPO.

[Creating a MPO](#creating-a-mpo)

The module `mps` includes also the definition of a basic `MPO` class. An empty `MPO` object is created as
```
aMPO=MPO();
```
The operators can be initialized obe by one, changing the elements in the list `MPO.Ms`, each of which should be a 4-index tensor with indices ordered as `(d1,Dl,d2,Dr)`, where `d1` and `d2` are the outgoing and incoming physical dimensions (resp. up and down) and `Dl` and `Dr` the left and right bond dimensions. Notice that to do this, one first needs to initialize the length of the MPO with `MPO.setLength(N)`.

For the following examples we use the simpler initialization methods for systems with homgeneous physical dimension:

 - `initializeFromNNterms(H,d,cutoff=1E-8)` constructs a `MPO` for the sum of nearest-neighbour terms, where arguments
   - `H` specifies a list of two-site operators; its length (N-1) determines the size of the system (N);
   - `d` should be the physical dimension of one site (i.e. each term in `H`has to be dimension $d^2 \times d^2$);
   - `cutoff` (optional, default value $10^{-8}$) is used to discard singular values (in the SVD of each term) which are (in relative value w.r.t. the largest one) below this value.


Additionally,

 - `MPO.identityMPO(length,physical_dim)` (class method) returns the identity operator for a of `length` where all sites have the same `physical_dim`

Similar to the `MPS` class, `printMPO()` explicitly shows the shapes of individual tensors. 

To compute the expectation value of a `MPO`, or a matrix elements between `MPS`, we can use the following method:
```
contractor.contractBraMPOKet(bra,oper,ket)
```

In [ ]:
# Parameters of the problem
N=16;
d=2;

J=1.;
g=1.;

# A list of 2-body operators in the Hamiltonian (could be done with np.kron):
# leftmost term
hL=J*op.twoBodyOperator(sigmaZ,sigmaZ)+g*op.twoBodyOperator(sigmaX,sigma0)+(g/2)*op.twoBodyOperator(sigma0,sigmaX);
# bulk terms
h=J*op.twoBodyOperator(sigmaZ,sigmaZ)+(g/2)*op.twoBodyOperator(sigmaX,sigma0)+(g/2)*op.twoBodyOperator(sigma0,sigmaX);
# rightmost term
hR=J*op.twoBodyOperator(sigmaZ,sigmaZ)+(g/2)*op.twoBodyOperator(sigmaX,sigma0)+g*op.twoBodyOperator(sigma0,sigmaX);

# The whole list
H=[hL,*([h]*(N-3)),hR];

# The MPO form
Hmpo=MPO();
Hmpo.initializeFromNNterms(H,d);

## Exact solution

If the system is small enough ($N\leq 20$) we can solve the problem exactly.

In [ ]:
# Test the Hamiltonian with exact diagonalization. We will use sparse matrices functionality, included in scipy

from scipy import sparse
from scipy.sparse.linalg import eigsh

# The many-body operator as sparse matrix
fullH=op.expandNNHamiltonian(d,N,H);

if not fullH==None:
    # To make the lowest eigenvalue that of largest magnitude, and speed it up a bit, we shift the Hamiltonian
    offset=N/2
    %time S,U=eigsh(fullH-offset*sparse.eye(np.power(d,N)),which='LM')
    S=S+offset;
    Egs_exact=min(S);
    print('Exact GS energy is ',Egs_exact);
else:
    Egs_exact=None;

## Imaginary time evolution with TEBD


We can use the TEBD algorithm to evolve an initial state in imaginary time and approximate the ground state of the system.

The code provides an object ```TEBD``` that runs  time evolution. To setup the problem, we initialize the object with a NN Hamiltonian  given as a list of terms (as constructed above). Optionally, we can also specify an initial state.

```python
initialize(d=2,D=10,N=10,order=1,delta=0.01,hamiltonian=None,cutoff=1E-10)
```
where 
 - `order` is the Trotter order; supported are only first(1) or second(2)
 - `cutoff` is an optional argument that determines how Schmidt values are inverted (discarded if smaller than the cutoff)
 - `hamiltonian` should be a list of local operators (as `H` in the example above), but can be initialized independently using ```initializeHamiltonian(hamiltonian)```. 

To run a single step of time evolution, we can use the method
```python
runTimeEvolutionStep(state,delta=None,imaginaryTime=True,order=None,D=None,forceCanonical=True)
```

where
 - `state` is the initial state (a MPS) and will be modified by the function (dimensions should agree with those of the stored Hamiltonian),
 - `imaginaryTime` can be used to select imaginary (`True`) or real (`False`) time,
 - `forceCanonical`, if `True` (default), ensures the canonical form is enforced before the time step.
and the returned value is the modified MPS (also stored in `TEBD.state`)

To search for the ground state, we can 
1. set a time step,
2. evolve in imaginary time for a certain number of steps,
3. check the energy value to decide convergence.

The code provides a function that performs such convergence tests in the TEBD method:

```python
logdata = runImaginaryTimeEvolution(state,nr_steps=None,delta=None,tol=1E-8,saving_freq=10,D=None,logdata=np.empty(0))
```

Arguments:
 - `nr_steps` -> fixed number of steps in the evolution. If not given, the algorithm runs until energy is converged to tol in relative value.

 - `delta` -> time step. If not given, the previous value (or the one given in initialize) is used.

 - `tol` -> specifies the convergence criterion (in relative value of E) when not running for fixed number of steps.

 - `saving_freq` -> frequency with which energy is written to log during the evolution. 

 - `D` -> bond dimension (if not given, the last one or the one given in initialize is used).
 
 - `logdata` -> array to log results (see below); if a non-empty array is given as argument, it should either be empty (in which case, it is initialzed now) or a matrix with 4 columns, in which case the new results are appended to it, and time is increasing from the last recorded value.

We can read and plot the evolution of the energy from the returned `log` array, which contains the following columns:
 - number of steps, 
 - total imaginary time
 - expectation value of the Hamiltonian $\langle H \rangle$
 - norm $\langle \Psi | \Psi \rangle$
 

[Running the algorithm](#running-the-algorithm)

The next cells illustrate how to use this functions with an example.

**1.** We run the algorithm starting from a random MPS and with a fixed time step until energy converges.

In [ ]:
D=10;

# Initialize a random state 
anMPS=MPS();
anMPS.initializeRandom(N,d,D);
anMPS.gaugeCondition('canonical',1);

# Check the initial energy
resH=contractor.contractBraMPOKet(anMPS,Hmpo,anMPS);
print('Initial energy:',resH)

orderT=2;
algorithm=TEBD();
algorithm.initialize(d,D,N,order=orderT,hamiltonian=H); 
#algorithm.setTruncationScheme('zip');

data=np.empty(0);
step=1.;
data=algorithm.runImaginaryTimeEvolution(anMPS,delta=step,saving_freq=1,logdata=data);
print('Final energy:',data[-1,2]/data[-1,3]);

# We can visualize the evolution of (normalized) energy during the algorithm in a plot:
if not Egs_exact==None:
    f2=plt.plot(data[:,0],Egs_exact*np.ones([data.shape[0],1]),'k',label='exact');
f1=plt.plot(data[:,1],data[:,2]/data[:,3],'b',label='step=1.');
plt.xlabel('imaginary time');
#plt.ylim(-15,-14.4); # zoom in the region of the GS
plt.legend();


__2.__ To improve precision, we decrease the time step. We can continue the evolution from the existing MPS, as follows, or reinitialize the algorithm.

In [ ]:
data=algorithm.runImaginaryTimeEvolution(anMPS,delta=.5,saving_freq=1,logdata=data);
print('Final energy:',data[-1,2]/data[-1,3]);

# We can visualize the full evolution:
if not Egs_exact==None:
    f2=plt.plot(data[:,1],Egs_exact*np.ones([data.shape[0],1]),'k',label='exact');
f1=plt.plot(data[:,1],data[:,2]/data[:,3],'b',label='step=1.');
plt.xlabel('imaginary time');
#plt.ylim(-15,-14)
plt.legend();

#### Question:

What happens if we instead *increase* the time step (i.e. run with larger `delta` after it was converged with a smaller one)? Why?

__3.__ We can sequentially decrease the time step to approximate better the ground state. We can also increase the bond dimension until the desired level of convergence is achieved. The following example illustrates this procedure.

In [ ]:
anMPS.initializeRandom(N,d,D);

Ds=[10,20,40,60,80];
deltas=[1.,0.5,0.2,0.1,0.05,0.01,0.005];
orderT=2;
algorithm=TEBD();
algorithm.initialize(d,Ds[0],N,order=orderT,delta=1,hamiltonian=H); 
#algorithm.setTruncationScheme('zip');
data=np.empty(0);

# We run with decreasing steps, each of them until energy is converged
for delta in deltas:
    data=algorithm.runImaginaryTimeEvolution(anMPS,delta=delta,saving_freq=1,logdata=data);
    print('Final energy for step ',delta,':',data[-1,2]/data[-1,3]);

# For the latest stime step, we increase the bond dimension sequentially
for id in range(1,len(Ds)):
    data=algorithm.runImaginaryTimeEvolution(anMPS,D=Ds[id],saving_freq=1,logdata=data);
    print('Final energy for step ',delta,', D=',Ds[id],':',data[-1,2]/data[-1,3]);

In [ ]:
# We can visualize the full evolution:
if not Egs_exact==None:
    f2=plt.plot(data[:,1],Egs_exact*np.ones([data.shape[0],1]),'k',label='exact');
f1=plt.plot(data[:,1],data[:,2]/data[:,3],'b',label='tebd');
plt.xlabel('imaginary time');
# Adjust the limit of the plot as needed
#plt.ylim(-20.1,-19);
plt.legend();

## Exercises

Explore the ground state of the Ising chain near criticality:

For $J=1$, $g\in[0.5,0.95,1.05,1.5]$:

**1.** Use the algorithm to find the ground state for system chain $N\approx 100$

**2.** For a subsystem in the middle of the chain, compute and plot as a function of $x$ the connected two-point correlator (recall first notebook):
    $$C_{zz}(x):=\langle \sigma_z^{[i]} \sigma_z^{[i+x]} \rangle- \langle \sigma_z^{[i]}\rangle \langle \sigma_z^{[i+x]} \rangle$$     
    
**3.** Plot the entropy of the half chain as a function of the system size $N\in[10,100]$ for $g=\{0.5,\ 1\}$. Is there an area law? Alternatively, for $N=100$, plot the entropy of a subchain in the center of the system, as a function of its size. 

Explore another nearest-neighbour Hamiltonian (e.g. Heisenberg, Ising with tilted field, Ising with disorder).
    